In [0]:
# Importing packages and initiating variables

from pyspark.sql import SparkSession
from pyspark.sql.types import StructType, StructField, StringType
from pyspark.sql.functions import col, lit
import pandas as pd

port = 1433
server = "xlc-azu-eus2-eds-prd-dw-server01.database.windows.net"
database = "dw_xle_sz"
synapse_schema_suffix, adls_schema_suffix = "", "_polybase"
schemas = ["cad"]

In [0]:
# Function to run SELECT query on Synapse
def run_synapse_query(query):
  jdbcUrl = f"jdbc:sqlserver://{server}:{port};database={database};encrypt=true;trustServerCertificate=true;hostNameInCertificate=*.database.windows.net;loginTimeout=30"

  df = spark.read \
    .format("jdbc") \
    .option("url", jdbcUrl) \
    .option("query", query) \
    .option("user", "") \
    .option("password", "") \
    .load()

  return df


In [0]:
# Function to compare DataFrames (Table Structure)

def compare_table_structure(df1, df2):
  compared_df = (df1.withColumnRenamed("data_type", "adls_data_type")
                .join(df2.withColumnRenamed("data_type", "synapse_data_type"),
                      on = ["table_name", "col_name"], how = "inner")
                ).filter(col("synapse_data_type") != col("adls_data_type"))

  differences = {}
  for row in compared_df.collect():
    if row["adls_data_type"] != row["synapse_data_type"]:
      differences[row["col_name"]] = f"{row['synapse_data_type']} -> {row['adls_data_type']}"

  return str(differences)

In [0]:
# Compare rows, columns, data types and data for each table
products, table_names, synapse_size, adls_size, col_dtypes, syn_adls_rows, adls_syn_rows = [], [], [], [], [], [], []

for schema in schemas:
  synapse_schema, adls_schema = f"{schema}{synapse_schema_suffix}", f"{schema}{adls_schema_suffix}"
  
  table_query = f"""SELECT TABLE_NAME AS table_name FROM INFORMATION_SCHEMA.TABLES WHERE TABLE_SCHEMA = '{adls_schema}' """
  tables = run_synapse_query(table_query)
  
  for table in tables.collect():
    table_name = table["table_name"]

    try:
      synapse_row_count = run_synapse_query(f"SELECT COUNT(1) AS count FROM [{synapse_schema}].[{table_name}]").collect()[0]["count"]
      synapse_column_query = f"""SELECT
        TABLE_NAME AS table_name,
        COLUMN_NAME AS col_name, 
        CASE DATA_TYPE
          WHEN 'int' THEN DATA_TYPE
          WHEN 'char' THEN CONCAT(DATA_TYPE, '(', TRIM(STR(CHARACTER_MAXIMUM_LENGTH)), ')' )
          WHEN 'varchar' THEN CONCAT(DATA_TYPE, '(', TRIM(STR(CHARACTER_MAXIMUM_LENGTH)) ,')' )
          WHEN 'decimal' THEN CONCAT(DATA_TYPE, '(', TRIM(STR(NUMERIC_PRECISION)), ',', TRIM(STR(NUMERIC_SCALE)), ')' )
          ELSE DATA_TYPE END AS data_type
        FROM INFORMATION_SCHEMA.COLUMNS WHERE TABLE_NAME = '{table_name}' AND TABLE_SCHEMA = '{synapse_schema}' """
      synapse_columns = run_synapse_query(f"{synapse_column_query}")
      synapse_col_count = synapse_columns.count()
      synapse_rc = (f"({synapse_row_count}, {synapse_col_count})")
      synapse_adls_data_match_query = f"""SELECT * FROM [{synapse_schema}].[{table_name}] EXCEPT SELECT * FROM [{adls_schema}].[{table_name}]"""
      synapse_adls_data = run_synapse_query(synapse_adls_data_match_query).count()
      compared_columns = "-"
    
    except:
      synapse_row_count, synapse_col_count, compared_columns, adls_synapse_data, synapse_adls_data = "-", "-", "{}", "-", "-"

    adls_row_count = run_synapse_query(f"SELECT COUNT(1) AS count FROM [{adls_schema}].[{table_name}]").collect()[0]["count"]
    adls_column_query = f"""SELECT
      TABLE_NAME AS table_name,
      COLUMN_NAME AS col_name, 
      CASE DATA_TYPE
        WHEN 'int' THEN DATA_TYPE
        WHEN 'char' THEN CONCAT(DATA_TYPE, '(', TRIM(STR(CHARACTER_MAXIMUM_LENGTH)), ')' )
        WHEN 'varchar' THEN CONCAT(DATA_TYPE, '(', TRIM(STR(CHARACTER_MAXIMUM_LENGTH)) ,')' )
        WHEN 'decimal' THEN CONCAT(DATA_TYPE, '(', TRIM(STR(NUMERIC_PRECISION)), ',', TRIM(STR(NUMERIC_SCALE)), ')' )
        ELSE DATA_TYPE END AS data_type
      FROM INFORMATION_SCHEMA.COLUMNS WHERE TABLE_NAME = '{table_name}' AND TABLE_SCHEMA = '{adls_schema}' """
    adls_columns = run_synapse_query(f"{adls_column_query}")
    adls_col_count = adls_columns.count()
    adls_rc = (f"({adls_row_count}, {adls_col_count})")

    if compared_columns == "-":
      adls_synapse_data_match_query = f"""SELECT * FROM [{adls_schema}].[{table_name}] EXCEPT SELECT * FROM [{synapse_schema}].[{table_name}]"""
      adls_synapse_data = run_synapse_query(adls_synapse_data_match_query).count()
      compared_columns = compare_table_structure(adls_columns, synapse_columns)
    
    products.append(f"{schema}")
    table_names.append(f"{table_name}")
    synapse_size.append(synapse_rc)
    adls_size.append(adls_rc)
    col_dtypes.append(compared_columns)
    syn_adls_rows.append(synapse_adls_data)
    adls_syn_rows.append(adls_synapse_data)

data = {
  'product': products,
  'table_name': table_names,
  'synapse_size': synapse_size,
  'adls_size': adls_size,
  'synapse_adls_dtypes_mismatch': col_dtypes,
  'synapse-adls_mismatch_rows': syn_adls_rows,
  'adls-synapse_mismatch_rows': adls_syn_rows
  }

final_df = pd.DataFrame(data)
display(final_df)

--------------------------------------------------------------------------- 
 Py4JJavaError Traceback (most recent call last)
 <command-1381023441571321> in <module> 
 6 
 7 table_query = f"""SELECT TABLE_NAME AS table_name FROM INFORMATION_SCHEMA.TABLES WHERE TABLE_SCHEMA = '{adls_schema}' """ 
 ----> 8 tables = run_synapse_query ( table_query ) 
 9 
 10 for table in tables . collect ( ) : 

 <command-1381023441571319> in run_synapse_query (query) 
 3 jdbcUrl = f"jdbc:sqlserver://{server}:{port};database={database};encrypt=true;trustServerCertificate=true;hostNameInCertificate=*.database.windows.net;loginTimeout=30" 
 4 
 ----> 5 df = spark . read \ 
 6 . format ( "jdbc" ) \ 
 7 . option ( "url" , jdbcUrl ) \ 

 /databricks/spark/python/pyspark/sql/readwriter.py in load (self, path, format, schema, **options) 
 162 return self . _df ( self . _jreader . load ( self . _spark . _sc . _jvm . PythonUtils . toSeq ( path ) ) ) 
 163 else : 
 --> 164 return self . _df ( self . _jreader . load ( ) ) 
 165 
 166 def json(self, path, schema=None, primitivesAsString=None, prefersDecimal=None,

 /databricks/spark/python/lib/py4j-0.10.9.1-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1302 
 1303 answer = self . gateway_client . send_command ( command ) 
 -> 1304 return_value = get_return_value(
 1305 answer, self.gateway_client, self.target_id, self.name)
 1306 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 115 def deco ( * a , ** kw ) : 
 116 try : 
 --> 117 return f ( * a , ** kw ) 
 118 except py4j . protocol . Py4JJavaError as e : 
 119 converted = convert_exception ( e . java_exception ) 

 /databricks/spark/python/lib/py4j-0.10.9.1-src.zip/py4j/protocol.py in get_return_value (answer, gateway_client, target_id, name) 
 324 value = OUTPUT_CONVERTER [ type ] ( answer [ 2 : ] , gateway_client ) 
 325 if answer [ 1 ] == REFERENCE_TYPE : 
 --> 326 raise Py4JJavaError(
 327 "An error occurred while calling {0}{1}{2}.\n" . 
 328 format(target_id, ".", name), value)

 Py4JJavaError : An error occurred while calling o588.load.
: com.microsoft.sqlserver.jdbc.SQLServerException: Login failed for user ''. ClientConnectionId:d9379c94-7971-42d0-90b9-9610f08025a9
	at com.microsoft.sqlserver.jdbc.SQLServerException.makeFromDatabaseError(SQLServerException.java:262)
	at com.microsoft.sqlserver.jdbc.TDSTokenHandler.onEOF(tdsparser.java:283)
	at com.microsoft.sqlserver.jdbc.TDSParser.parse(tdsparser.java:129)
	at com.microsoft.sqlserver.jdbc.TDSParser.parse(tdsparser.java:37)
	at com.microsoft.sqlserver.jdbc.SQLServerConnection.sendLogon(SQLServerConnection.java:5333)
	at com.microsoft.sqlserver.jdbc.SQLServerConnection.logon(SQLServerConnection.java:4066)
	at com.microsoft.sqlserver.jdbc.SQLServerConnection.access$000(SQLServerConnection.java:85)
	at com.microsoft.sqlserver.jdbc.SQLServerConnection$LogonCommand.doExecute(SQLServerConnection.java:4004)
	at com.microsoft.sqlserver.jdbc.TDSCommand.execute(IOBuffer.java:7418)
	at com.microsoft.sqlserver.jdbc.SQLServerConnection.executeCommand(SQLServerConnection.java:3272)
	at com.microsoft.sqlserver.jdbc.SQLServerConnection.connectHelper(SQLServerConnection.java:2768)
	at com.microsoft.sqlserver.jdbc.SQLServerConnection.login(SQLServerConnection.java:2418)
	at com.microsoft.sqlserver.jdbc.SQLServerConnection.connectInternal(SQLServerConnection.java:2265)
	at com.microsoft.sqlserver.jdbc.SQLServerConnection.connect(SQLServerConnection.java:1291)
	at com.microsoft.sqlserver.jdbc.SQLServerDriver.connect(SQLServerDriver.java:881)
	at org.apache.spark.sql.execution.datasources.jdbc.connection.BasicConnectionProvider.getConnection(BasicConnectionProvider.scala:49)
	at org.apache.spark.sql.execution.datasources.jdbc.connection.ConnectionProviderBase.create(ConnectionProvider.scala:102)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$createConnectionFactory$1(JdbcUtils.scala:69)
	at org.apache.spark.sql.execution.datasources.jdbc.JDBCRDD$.getQueryOutputSc

In [0]:

synapse_schema = 'gismo_btl'
table_name = 't_ax_supp_policy_details'
adls_schema = 'dw_btl_gismo'
table_name_adls = 't_ax_supp_policy_details'
# table_query = f"""SELECT TABLE_NAME AS table_name FROM INFORMATION_SCHEMA.TABLES WHERE TABLE_SCHEMA = '{synapse_schema}' """
table_query = f"""select * from {synapse_schema}.{table_name}"""
df = run_synapse_query(table_query)
df.createOrReplaceTempView(f"""{table_name}_vw_rs""")





#### compare the columns
synapse_tbl_column = df.columns

df = spark.sql("describe table dw_btl_rdapp.claim_metrics")
adls_column_list = [row.col_name for row in df.select('col_name').collect()]
diff_columns = set(synapse_tbl_column) - set(adls_column_list)
if diff_columns:
  print('column mismatch, the difference', diff_columns)

syn_count = run_synapse_query(f'select * from {synapse_schema}.{table_name}').count()
adls_count = spark.sql(f'select count(*) from {adls_schema}.{table_name_adls}').count()



column mismatch, the difference {'incoming_office_region_l2', 'primary_layer', 'incept_to_issue_days', 'insured_client', 'gismo_line_of_business', 'pfo_date', 'layering_flag', 'policy_inception_date', 'underwriting_assistant', 'last12months3matured', 'quote_number', 'parent_client_name', 'modifiedhandoverdate', 'invoice_issue_date', 'underwriting_year', 'endorsement_date', 'incoming_office_region_l1', 'program_currency', 'brokeraddref', 'incoming_producing', 'run_date', 'master_broker_group', 'network_partner_instruction_date', 'true_gp', 'net_ceded_premium', 'policy_id', 'layered_policies', 'endorsement_number', 'incept_to_instruct_days', 'instruct_to_issue_days', 'fir_to_instruct_days', 'local_currency', 'policy_current_status', 'policy_identification', 'date_premium_received_by_np', 'rsr_date', 'incoming_office_type_descr', 'gismo_local_plcy_id', 'pending_due_yn', 'local_broker_group', 'global_program_number', 'edit_date', 'fir_to_issue_days', 'contract_type_code', 'pfx_date', 'prod

In [0]:
%sql
describe dw_btl_gismo.t_ax_supp_policy_details;

col_name data_type comment policy_number string null endorsement_number string null policy_identification string null policy_current_status string null global_program_number string null account_name string null insured_client string null local_broker_group varchar(100) null master_broker_group varchar(100) null captive_flag boolean null cpc_flag string null tier1_flag string null producing_gls_flag string null incoming_gls_flag varchar(100) null rejected_yn string null pending_due_yn string null policy_lead_follow varchar(25) null primary_layer string null pol_n_r_flag varchar(50) null prog_new_renew_flag boolean null mainline varchar(100) null gismo_line_of_business string null product_line varchar(100) null insured_country varchar(255) null incoming_office_type_descr string null incoming_office_region_l1 string null incoming_office_region_l2 string null producing_country_code varchar(10) null country_of_settlement varchar(100) null prod_office_sub_region varchar(100) null prod_office_region varchar(100) null prod_segment_group varchar(100) null fronting_partner_name string null underwriting_year string null inception_year int null last12months string null last36monthsrevised string null last12months3matured string null policy_inception_date string null policy_expiry_date string null run_date string null draft_date string null edit_date string null in_review_date string null fir_date string null instructed_date string null network_partner_instruction_date string null modifiedhandoverdate string null pfx_date string null pdo_date string null peo_date string null pfo_date string null combined_issuance_date string null completed_date string null effective_date string null endorsement_date string null rsr_date string null invoice_issue_date string null date_premium_received_by_np string null incept_to_fir_days bigint null fir_to_instruct_days bigint null incept_to_instruct_days bigint null instruct_to_issue_days bigint null incept_to_issue_days bigint null fir_to_issue_days bigint null policy_unissued_for_days bigint null program_lead_follow string null flag_axa_business string null layered_policies boolean null layering_flag int null parent_client_name varchar(350) null quote_number string null program_duns varchar(50) null policy_duns varchar(50) null underwriting_assistant string null pam string null puw_program_underwriter varchar(255) null network_partner_owner string null contract_type_code varchar(20) null incoming_producing varchar(10) null true_gp string null brokeraddref varchar(15) null net_ceded_premium decimal(38,18) null local_currency string null policy_rate_of_exchange decimal(38,18) null program_currency string null gismo_local_plcy_id string null policy_id int null gismo_office_country string null

In [0]:
synapse_query = "SELECT COLUMN_NAME, DATA_TYPE, CHARACTER_MAXIMUM_LENGTH FROM INFORMATION_SCHEMA.COLUMNS WHERE TABLE_NAME = 't_ax_supp_policy_gismo_local_policy' AND TABLE_SCHEMA = 'gismo_btl'"
df = run_synapse_query(synapse_query)
display(df)

COLUMN_NAME DATA_TYPE CHARACTER_MAXIMUM_LENGTH

In [0]:

syn_count = run_synapse_query(f'select * from {synapse_schema}.{table_name}').count()
adls_count = spark.sql(f'select * from {adls_schema}.{table_name_adls}').count()
print(syn_count)
print(adls_count)


187720
187720


In [0]:
diff_df = spark.sql(f"""
                    select policy_rate_of_exchange from gismo_btl.t_ax_supp_policy_details
                    minus 
                    select policy_rate_of_exchange from dw_btl_gismo.t_ax_supp_policy_details
                    """
)

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-453372701124406>, line 1
----> 1 diff_df = spark.sql(f"""
      2                     select policy_rate_of_exchange from gismo_btl.t_ax_supp_policy_details
      3                     minus 
      4                     select policy_rate_of_exchange from dw_btl_gismo.t_ax_supp_policy_details
      5                     """
      6 )

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
     50         module_name, class_name, function_name, time.perf_counter() - start, signature
     51     )
     52     return res

File /databricks/spark/python/pyspark/sql/session.py:1602, in SparkSession.sql(self, sqlQuery, args, **kwargs)
   1598      

In [0]:
%sql
select * from {table_name}_vw_rs;

com.databricks.backend.common.rpc.SparkDriverExceptions$SQLExecutionException: org.apache.spark.sql.catalyst.parser.ParseException: 
[PARSE_SYNTAX_ERROR] Syntax error at or near '{'.(line 1, pos 14)

== SQL ==
select * from {table_name}_vw_rs
--------------^^^

	at org.apache.spark.sql.catalyst.parser.ParseException.withCommand(parsers.scala:259)
	at org.apache.spark.sql.catalyst.parser.AbstractParser.parse(parsers.scala:98)
	at org.apache.spark.sql.execution.SparkSqlParser.parse(SparkSqlParser.scala:111)
	at org.apache.spark.sql.catalyst.parser.AbstractSqlParser.parsePlan(AbstractSqlParser.scala:87)
	at com.databricks.sql.parser.DatabricksSqlParser.$anonfun$parsePlan$1(DatabricksSqlParser.scala:77)
	at com.databricks.sql.parser.DatabricksSqlParser.parse(DatabricksSqlParser.scala:98)
	at com.databricks.sql.parser.DatabricksSqlParser.parsePlan(DatabricksSqlParser.scala:74)
	at org.apache.spark.sql.SparkSession.$anonfun$sql$6(SparkSession.scala:919)
	at com.databricks.spark.util.FrameProfiler$.record(FrameProfiler.scala:94)
	at org.apache.spark.sql.catalyst.QueryPlanningTracker.measurePhase(QueryPlanningTracker.scala:383)
	at org.apache.spark.sql.SparkSession.$anonfun$sql$5(SparkSession.scala:918)
	at org.apache.spark.sql.SparkSession.withActive(SparkSession.scala:1148)
	at org.apache.spark.sql.SparkSession.sql(SparkSession.scala:917)
	at org.apache.spark.sql.SparkSession.$anonfun$sql$9(SparkSession.scala:951)
	at org.apache.spark.sql.SparkSession.withActive(SparkSession.scala:1148)
	at org.apache.spark.sql.SparkSession.sql(SparkSession.scala:951)
	at org.apache.spark.sql.SparkSession.sql(SparkSession.scala:984)
	at org.apache.spark.sql.SQLContext.sql(SQLContext.scala:695)
	at com.databricks.backend.daemon.driver.DriverLocal$DbClassicStrategy.executeSQLQuery(DriverLocal.scala:237)
	at com.databricks.backend.daemon.driver.DriverLocal.executeSQLSubCommand(DriverLocal.scala:319)
	at com.databricks.backend.daemon.driver.DriverLocal.$anonfun$executeSql$1(DriverLocal.scala:338)
	at scala.collection.immutable.List.map(List.scala:293)
	at com.databricks.backend.daemon.driver.DriverLocal.executeSql(DriverLocal.scala:333)
	at com.databricks.backend.daemon.driver.JupyterDriverLocal.repl(JupyterDriverLocal.scala:714)
	at com.databricks.backend.daemon.driver.DriverLocal.$anonfun$execute$34(DriverLocal.scala:1012)
	at com.databricks.unity.EmptyHandle$.runWith(UCSHandle.scala:128)
	at com.databricks.backend.daemon.driver.DriverLocal.$anonfun$execute$23(DriverLocal.scala:1003)
	at com.databricks.logging.UsageLogging.$anonfun$withAttributionContext$1(UsageLogging.scala:426)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.AttributionContext$.withValue(AttributionContext.scala:196)
	at com.databricks.logging.UsageLogging.withAttributionContext(UsageLogging.scala:424)
	at com.databricks.logging.UsageLogging.withAttributionContext$(UsageLogging.scala:418)
	at com.databricks.backend.daemon.driver.DriverLocal.withAttributionContext(DriverLocal.scala:69)
	at com.databricks.logging.UsageLogging.withAttributionTags(UsageLogging.scala:470)
	at com.databricks.logging.UsageLogging.withAttributionTags$(UsageLogging.scala:455)
	at com.databricks.backend.daemon.driver.DriverLocal.withAttributionTags(DriverLocal.scala:69)
	at com.databricks.backend.daemon.driver.DriverLocal.execute(DriverLocal.scala:958)
	at com.databricks.backend.daemon.driver.DriverWrapper.$anonfun$tryExecutingCommand$2(DriverWrapper.scala:859)
	at scala.util.Try$.apply(Try.scala:213)
	at com.databricks.backend.daemon.driver.DriverWrapper.$anonfun$tryExecutingCommand$1(DriverWrapper.scala:851)
	at com.databricks.backend.daemon.driver.DriverWrapper.$anonfun$tryExecutingCommand$3(DriverWrapper.scala:891)
	at com.databricks.logging.UsageLogging.executeThunkAndCaptureResultTags$1(UsageLogging.scala:667)
	at com.databricks.logging.UsageLogging.$anonfun$recordOperationWithResultTags$4(UsageLogging.scala:685)
	at com.databricks.logging.UsageLogging.$anon

In [0]:
df = spark.sql("Select net_ceded_premium from dw_btl_gismo.t_ax_supp_policy_details");
display(df)

net_ceded_premium 2975.000000000000000000 14337.990234375000000000 2700.000000000000000000 2125.000000000000000000 116070.046875000000000000 -647.190002441406200000 7943.609863281250000000 645537.125000000000000000 1700.000000000000000000 1703.750000000000000000 6969.930175781250000000 1684.939941406250000000 0E-18 1696.109985351562500000 2055.370117187500000000 2952.409912109375000000 1100.000000000000000000 3885.669921875000000000 3885.669921875000000000 9339.330078125000000000 1698.800048828125000000 1629.800048828125000000 2800.000000000000000000 7777.200195312500000000 7777.200195312500000000 15422.400390625000000000 15422.400390625000000000 15422.400390625000000000 7645.200195312500000000 3073.300048828125000000 5394.450195312500000000 1637.130004882812500000 1893.760009765625000000 8001.250000000000000000 868.250000000000000000 7440.430175781250000000 1538.140014648437500000 1896.630004882812500000 1170.000000000000000000 10980.349609375000000000 10969.370117187500000000 11032.410156250000000000 10219.650390625000000000 9340.099609375000000000 9525.250000000000000000 1892.500000000000000000 39002.628906250000000000 39002.628906250000000000 1674.839965820312500000 1475.369995117187500000 1855.839965820312500000 8000.000000000000000000 -600.000000000000000000 2271.949951171875000000 1616.449951171875000000 1616.449951171875000000 6188.229980468750000000 17153.300781250000000000 17153.300781250000000000 29803.490234375000000000 4497.549804687500000000 1710.000000000000000000 1710.000000000000000000 1710.000000000000000000 1440.239990234375000000 1058.140014648437500000 1058.140014648437500000 2875.000000000000000000 2100.000000000000000000 1119.199951171875000000 1924.910034179687500000 27227.220703125000000000 72503.648437500000000000 8691.969726562500000000 25571.349609375000000000 15693.120117187500000000 15693.120117187500000000 25571.349609375000000000 1937.969970703125000000 2200.000000000000000000 28798.300781250000000000 1520.479980468750000000 4555.000000000000000000 4502.959960937500000000 4730.779785156250000000 1960.000000000000000000 2882.500000000000000000 2882.500000000000000000 3741.189941406250000000 1411.140014648437500000 27360.029296875000000000 8823.389648437500000000 1341.500000000000000000 1600.000000000000000000 2939.000000000000000000 2719.060058593750000000 1722.479980468750000000 1722.479980468750000000 1402.829956054687500000 1402.829956054687500000 2400.000000000000000000 4032.260009765625000000 0E-18 1350.500000000000000000 2100.000000000000000000 2100.000000000000000000 1899.949951171875000000 942.349975585937500000 19647.619140625000000000 2500.000000000000000000 1200.000000000000000000 2500.000000000000000000 2500.000000000000000000 28238.839843750000000000 5400.000000000000000000 1710.000000000000000000 18606.910156250000000000 18606.910156250000000000 3558.000000000000000000 2100.000000000000000000 2100.000000000000000000 2100.000000000000000000 1875.199951171875000000 3790.000000000000000000 3790.000000000000000000 5292.750000000000000000 -4834.000000000000000000 2875.260009765625000000 2875.260009765625000000 2100.000000000000000000 5056.060058593750000000 5056.060058593750000000 4381.580078125000000000 2000.000000000000000000 1625.000000000000000000 1996.010009765625000000 1996.010009765625000000 3068.270019531250000000 2989.520019531250000000 1266.300048828125000000 1713.750000000000000000 1473.750000000000000000 1473.750000000000000000 6930.000000000000000000 -2752.770019531250000000 365446.250000000000000000 8753.410156250000000000 8753.410156250000000000 2500.000000000000000000 1710.000000000000000000 1710.000000000000000000 3600.000000000000000000 2270.709960937500000000 3581.209960937500000000 4000.000000000000000000 63319.031250000000000000 1725.000000000000000000 1565.630004882812500000 2317.580078125000000000 1350.000000000000000000 920.820007324218800000 949.780029296875000000 16073.889648437500000000 -750.000000000000000000 2558.600097656250000000 9948.000000000000000000 994

In [0]:
df = spark.sql(f"SELECT net_ceded_premium FROM {table_name}_vw_rs");
display(df)

net_ceded_premium 2625.000000000000000000 2700.000000000000000000 1275.000000000000000000 2975.000000000000000000 4250.000000000000000000 2125.000000000000000000 6882.390136718750000000 2550.000000000000000000 5451.589843750000000000 2454.800048828125000000 4400.000000000000000000 1700.000000000000000000 3965.250000000000000000 1350.000000000000000000 33500.000000000000000000 3570.000000000000000000 1700.000000000000000000 2500.000000000000000000 3000.000000000000000000 2340.000000000000000000 2533.500000000000000000 7508.209960937500000000 1700.000000000000000000 6187.580078125000000000 6631.180175781250000000 2662.810058593750000000 118932.000000000000000000 25000.000000000000000000 1700.000000000000000000 2807.800048828125000000 169118.203125000000000000 2125.000000000000000000 2125.000000000000000000 4908.240234375000000000 3131.500000000000000000 13436.379882812500000000 2125.000000000000000000 2125.000000000000000000 1700.000000000000000000 2807.800048828125000000 5000.000000000000000000 8061.410156250000000000 4983.580078125000000000 2805.000000000000000000 17850.000000000000000000 9000.000000000000000000 2465.000000000000000000 15320.599609375000000000 75000.000000000000000000 3236.370117187500000000 3000.000000000000000000 6375.000000000000000000 1275.000000000000000000 2550.000000000000000000 1237.500000000000000000 3400.000000000000000000 7726.500000000000000000 201200.000000000000000000 191155.078125000000000000 1763.750000000000000000 5823.580078125000000000 4250.000000000000000000 17212.500000000000000000 2168.909912109375000000 2500.000000000000000000 2236.989990234375000000 1500.000000000000000000 13600.000000000000000000 1500.000000000000000000 3000.000000000000000000 2975.000000000000000000 2500.000000000000000000 3190.469970703125000000 3825.000000000000000000 3400.000000000000000000 1361.250000000000000000 2500.000000000000000000 2100.000000000000000000 2500.000000000000000000 2250.000000000000000000 2802.739990234375000000 2500.000000000000000000 2125.000000000000000000 2125.000000000000000000 2975.000000000000000000 2125.000000000000000000 2125.000000000000000000 2000.000000000000000000 5355.000000000000000000 2125.000000000000000000 3825.000000000000000000 7748.299804687500000000 2500.000000000000000000 1485.000000000000000000 5850.000000000000000000 1275.000000000000000000 7500.000000000000000000 2500.000000000000000000 3978.290039062500000000 42297.128906250000000000 50000.000000000000000000 25000.000000000000000000 2125.000000000000000000 2125.000000000000000000 2125.000000000000000000 1500.000000000000000000 11296.500000000000000000 5202.339843750000000000 2125.000000000000000000 2125.000000000000000000 1770.829956054687500000 2830.300048828125000000 2125.000000000000000000 1700.000000000000000000 4250.000000000000000000 1530.000000000000000000 1700.000000000000000000 1530.000000000000000000 2125.000000000000000000 2456.540039062500000000 3421.250000000000000000 15492.299804687500000000 11004.669921875000000000 4368.580078125000000000 2125.000000000000000000 25000.000000000000000000 4849.540039062500000000 2125.000000000000000000 4070.560058593750000000 2000.000000000000000000 7204.049804687500000000 2406.310058593750000000 2125.000000000000000000 2125.000000000000000000 1530.000000000000000000 5507.149902343750000000 1700.000000000000000000 8370.000000000000000000 1530.000000000000000000 2125.000000000000000000 50000.000000000000000000 13330.320312500000000000 7500.000000000000000000 2125.000000000000000000 3145.000000000000000000 3306.379882812500000000 2500.000000000000000000 1530.000000000000000000 2550.000000000000000000 5355.000000000000000000 273219.750000000000000000 24534.240234375000000000 1119.109985351562500000 2125.000000000000000000 11050.000000000000000000 2125.000000000000000000 1900.000000000000000000 6953.759765625000000000 2125.000000000000000000 8606.250000000000000000 4325.229980468750000000 3000.000000000000000000 2500.000000000000000000 2125.000000000000000000 2125.000000000000

In [0]:
display(diff_df)

Claim Identifier Claim Number Global Claim Number Claim Incident Date Claim Cause of Loss Description Claim Status Description Planning Line of Business Name Large Catastrophe Attritional Threat Code Claim Event Code Claim Event Name Bulk Bordereaux Indicator 22821886 M990902747 0000125317 1900-01-01 Unknown Unknown CAT UNM Unmapped 23024578 N40020680300 1900-01-01 Unknown Unknown CAT UKN Unknown 22698539 N60053630103 0000197992 1900-01-01 Unknown Unknown CAT UNM Unmapped 22715753 N60051550302 0000196631 1900-01-01 Unknown Unknown Large UNM Unmapped 23324995 N60163691101 0000244569 1900-01-01 Unknown Unknown Large UNM Unmapped 23134235 A61026640998 0000032199 1900-01-01 Unknown Unknown Large UNM Unmapped 23422389 A61018540901 0000029632 1900-01-01 Unknown Unknown Large UNM Unmapped 23132401 A60008560204 0000012910 1900-01-01 Unknown Unknown Large UNM Unmapped 22940143 N60062651199 0000203630 1900-01-01 Unknown Unknown CAT UNM Unmapped 22933820 M020103082 1900-01-01 Unknown Unknown Large UKN Unknown 22787814 N60119421001 1900-01-01 Unknown Unknown CAT UKN Unknown 23304611 N60159471101 0000244045 1900-01-01 Unknown Unknown Large UNM Unmapped 23130982 N60087580402 1900-01-01 Unknown Unknown CAT UKN Unknown 22705065 M050301175 1900-01-01 Unknown Unknown CAT UKN Unknown 22853150 M130500475 0003188021 1900-01-01 Unknown Unknown Large UKN Unknown 23426461 M991002686 1900-01-01 Unknown Unknown Large UKN Unknown 23036013 M040301889 0000069728 1900-01-01 Unknown Unknown Large UKN Unknown 23222667 A21007600400 1900-01-01 Unknown Unknown Large UKN Unknown 25395230 N60008510100 1900-01-01 Unknown Unknown CAT UKN Unknown 23326947 M990201752 0000119341 1900-01-01 Unknown Unknown CAT UNM Unmapped 23459273 N20059700496 0000141852 1900-01-01 Unknown Unknown CAT UNM Unmapped 22778111 N60055471101 1900-01-01 Unknown Unknown Large UKN Unknown 23298509 N60048561199 0000193839 1900-01-01 Unknown Unknown CAT UNM Unmapped 22835206 N20034561198 0000140313 1900-01-01 Unknown Unknown CAT UNM Unmapped 23382834 N60118481196 1900-01-01 Unknown Unknown CAT UKN Unknown 23358133 A61009511000 0000025667 1900-01-01 Unknown Unknown Large UKN Unknown 23305918 N60137680900 1900-01-01 Unknown Unknown CAT UKN Unknown 22705534 M110302282 0000096855 1900-01-01 Unknown Unknown CAT UNM Unmapped 23008603 M990100620 0000274579 1900-01-01 Unknown Unknown CAT UNM Unmapped 23407196 A61018450697 0000030767 1900-01-01 Unknown Unknown Large UNM Unmapped 22799558 M051001166 0000074997 1900-01-01 Unknown Unknown CAT 155 Hurricane Katrina 22806293 M991100450 1900-01-01 Unknown Unknown CAT UKN Unknown 22952482 N60049670601 1900-01-01 Unknown Unknown CAT UKN Unknown 23410546 M950953973 1900-01-01 Unknown Unknown CAT UKN Unknown 22899556 N20106610896 1900-01-01 Unknown Unknown CAT UKN Unknown 23423458 N65040470296 0000255268 1900-01-01 Unknown Unknown CAT UNM Unmapped 22912833 M981200675 0000117487 1900-01-01 Unknown Unknown CAT UNM Unmapped 22819515 M981002597 0000116343 1900-01-01 Unknown Unknown CAT UNM Unmapped 23306593 N40002420497 1900-01-01 Unknown Unknown CAT UKN Unknown 23054084 N60108630399 0000232510 1900-01-01 Unknown Unknown CAT UKN Unknown 22832631 A61008560802 0000026221 1900-01-01 Unknown Unknown Large UNM Unmapped 22846831 M030102350 0000065004 1900-01-01 Unknown Unknown Large UKN Unknown 22786186 N60067521098 1900-01-01 Unknown Unknown CAT UKN Unknown 23020407 N60460501203 1900-01-01 Unknown Unknown Large UKN Unknown 22933472 M990202406 0000119584 1900-01-01 Unknown Unknown CAT UKN Unknown 22794657 M981100275 1900-01-01 Unknown Unknown CAT UKN Unknown 22769158 N60023491001 0000177869 1900-01-01 Unknown Unknown Large UNM Unmapped 22780066 N40006450201 1900-01-01 Unknown Unknown CAT UKN Unknown 23157515 M050900656 0000075561 1900-01-01 Unknown Unknown CAT 155 Hurricane Katrina 22782979 N60076650400 1900-01-01 Unknown Unknown CAT UKN Unknown 22912259 A61004670502 0000275234 1900-01-01 Unknown Unknown Large UKN Unknown 22738999 N60080490300 0000215662 1900-01-01 Unknown 

In [0]:
%sql
select * from btl_src.art_claims limit 10;

Claim_currency Claim_handling_office Claim_title ClaimantKey ClaimHandlerKey ClaimKey ClaimReference ClaimsCauseCategoryKey ClaimStatusKey Date_of_closing Date_of_loss Date_of_notification dAxaShareOfTotal dBase2ClaimExchangeRate dCurrentExpenses dCurrentExpensesLegal dCurrentExpensesReserve dCurrentIndemnity dCurrentIndemnityReserve dCurrentPaidTotal dCurrentReserveTotal dGrossTotalIncurred dInitialExpensesReserve dInitialIndemnityReserve dInitialReserve dRecovery dtpolicyperiodfrom EventKey Last_payment Loss_location_country LossTypeKey OfficeKey PolicyKey PolicyLocationKey PolicyReference sEventCode EUR Paris XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX-X 31311 45658 11929 0080212 11 2054 2001-11-19T00:00:00Z 2000-09-19T00:00:00Z 2000-09-26T00:00:00Z 100.000000 1.00000000 364.660000 364.660000 0.000000 0.000000 0.000000 364.660000 0.000000 364.660000 0.00 14483.00 14483.00 null 2004-01-01T00:00:00Z null 2001-11-19T00:00:00Z null null 7 58544 null 808008 null EUR Paris XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX-X 33671 45658 12256 0080213 11 2118 2002-10-04T00:00:00Z 2000-10-03T00:00:00Z 2000-10-06T00:00:00Z 100.000000 1.00000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.00 152.00 152.00 null 2000-03-21T00:00:00Z null 2002-10-04T00:00:00Z null null 7 65268 null 840944 null EUR Paris Date de cr?ation du dossier : 06/11/2000 33879 45658 11685 0080214 11 2054 2000-11-22T00:00:00Z 2000-10-23T00:00:00Z 2000-11-03T00:00:00Z 100.000000 1.00000000 364.660000 364.660000 0.000000 0.000000 0.000000 364.660000 0.000000 364.660000 0.00 6098.00 6098.00 null 2005-08-01T00:00:00Z null 2000-11-22T00:00:00Z null null 7 60869 null 811162 null EUR Paris Date de cr?ation du dossier : 13/11/2000 31483 45658 11446 0080215 11 2054 2000-12-04T00:00:00Z 2000-10-13T00:00:00Z 2000-10-18T00:00:00Z 100.000000 1.00000000 0.000000 0.000000 0.000000 274.410000 0.000000 274.410000 0.000000 274.410000 0.00 274.00 274.00 null 2004-12-01T00:00:00Z null 2000-12-04T00:00:00Z null null 7 58687 null 808267 null EUR Paris XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX-X 31877 45658 11447 0080216 11 2054 2006-10-16T00:00:00Z 2000-10-03T00:00:00Z 2000-10-18T00:00:00Z 100.000000 1.00000000 3152.800000 2554.800000 0.000000 18000.000000 0.000000 21152.800000 0.000000 21152.800000 0.00 7622.00 7622.00 null 2000-12-27T00:00:00Z null 2006-10-16T00:00:00Z null null 7 59144 null 809086 null EUR Paris XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX-X 32782 45658 11817 0080217 11 2118 2003-10-16T00:00:00Z 2000-03-14T00:00:00Z 2000-10-09T00:00:00Z 100.000000 1.00000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.00 7622.00 7622.00 null 1999-05-01T00:00:00Z null 2003-10-16T00:00:00Z null null 7 59848 null 810037 null EUR Paris XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX-X 33092 45658 12001 0080218 11 2054 2001-01-10T00:00:00Z 2000-10-23T00:00:00Z 2000-10-30T00:00:00Z 100.000000 1.00000000 0.000000 0.000000 0.000000 503.080000 0.000000 503.080000 0.000000 503.080000 0.00 1067.00 1067.00 null 2002-04-01T00:00:00Z null 2001-01-10T00:00:00Z null null 7 60288 null 810533 null EUR Paris XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX-X 33239 45658 10124 0080219 11 2118 2000-12-12T00:00:00Z 2000-09-01T00:00:00Z 2000-10-30T00:00:00Z 100.000000 1.00000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.00 3811.00 3811.00 null 2000-06-01T00:00:00Z null 2000-12-12T00:00:00Z null null 7 60373 null 810626 null EUR Paris XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX-X 33321 45658 11819 0080220 11 2118 2004-04-02T00:00:00Z 2000-10-24T00:00:00Z 2000-11-02T00:00:00Z 100.000000 1.00000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.000000 0.00 152.00 152.00 null 2002-06-01T00:00:00Z null 2004-04-02T00:00:00Z null null 7 60783 null 811070 null EUR Paris XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX-X 30818 45658 12254 0080221 11 2118 2003-08-12T00:00:00Z 2000-10-15T00:00:00Z 2000-10-26T00:00:00Z 100.000000 1.00000000 0.000000 0.000000 0.000000 0